In [1]:
import pandas as pd
from sqlalchemy import create_engine
import sqlalchemy
from sqlalchemy.ext.automap import automap_base
from sqlalchemy.orm import Session
from pprint import pprint
from sqlalchemy.sql import select
import json
from operator import itemgetter

In [2]:
file_one = "Table.csv"
df = pd.read_csv(file_one, encoding="ISO-8859-1")
df = df.dropna(subset = ['Type of data (a)'])
df = df.rename(columns={"Major area, region, country or area of destination": "Destination"})
df = df.rename(columns={'Unnamed: 6': "Total"})
del df['Sort\norder']
del df['Other South']
del df['Other North']
del df['Notes']
del df['Type of data (a)']
df.index = range(len(df))
df.to_csv("cleanedData.csv", header=True)
df.head()


Year Destination   Code      Total Afghanistan Albania Algeria  \
0  1990.0     Burundi  108.0    333,110          ..      ..      ..   
1  1990.0     Comoros  174.0     14,079          ..      ..      ..   
2  1990.0    Djibouti  262.0    122,221          ..      ..      ..   
3  1990.0     Eritrea  232.0     11,848          ..      ..      ..   
4  1990.0    Ethiopia  231.0  1,155,390          ..      ..      ..   

  American Samoa Andorra Angola   ...    Uruguay Uzbekistan Vanuatu  \
0             ..      ..     ..   ...         ..         ..      ..   
1             ..      ..     ..   ...         ..         ..      ..   
2             ..      ..     ..   ...         ..         ..      ..   
3             ..      ..    247   ...         ..         ..      ..   
4             ..      ..     ..   ...         ..         ..      ..   

  Venezuela (Bolivarian Republic of) Viet Nam Wallis and Futuna Islands  \
0                                 ..       ..                        ..   
1                                 ..       ..                        ..   
2                                 ..       ..                        ..   
3                                 ..       ..                        ..   
4                                 ..       ..                        ..   

  Western Sahara Yemen Zambia Zimbabwe  
0             ..    ..     ..       ..  
1             ..    ..     ..       ..  
2             ..   289     ..       ..  
3             ..    ..     91       82  
4             ..    68     ..       ..  

[5 rows x 236 columns]

In [3]:
df = pd.read_csv('cleanedData.csv')
engine = create_engine("sqlite:///MigrationData.sqlite")


In [4]:
df.head()

Unnamed: 0    Year Destination   Code      Total Afghanistan Albania  \
0           0  1990.0     Burundi  108.0    333,110          ..      ..   
1           1  1990.0     Comoros  174.0     14,079          ..      ..   
2           2  1990.0    Djibouti  262.0    122,221          ..      ..   
3           3  1990.0     Eritrea  232.0     11,848          ..      ..   
4           4  1990.0    Ethiopia  231.0  1,155,390          ..      ..   

  Algeria American Samoa Andorra   ...    Uruguay Uzbekistan Vanuatu  \
0      ..             ..      ..   ...         ..         ..      ..   
1      ..             ..      ..   ...         ..         ..      ..   
2      ..             ..      ..   ...         ..         ..      ..   
3      ..             ..      ..   ...         ..         ..      ..   
4      ..             ..      ..   ...         ..         ..      ..   

  Venezuela (Bolivarian Republic of) Viet Nam Wallis and Futuna Islands  \
0                                 ..       ..                        ..   
1                                 ..       ..                        ..   
2                                 ..       ..                        ..   
3                                 ..       ..                        ..   
4                                 ..       ..                        ..   

  Western Sahara Yemen Zambia Zimbabwe  
0             ..    ..     ..       ..  
1             ..    ..     ..       ..  
2             ..   289     ..       ..  
3             ..    ..     91       82  
4             ..    68     ..       ..  

[5 rows x 237 columns]

In [5]:
engine.table_names()
Base = automap_base()
Base.prepare(engine, reflect=True)
Base.classes.keys()

['mydata']

In [6]:
session = Session(engine) 
Mydata = Base.classes.mydata
conn = engine.connect()

In [7]:
select_data_2017 = select([Mydata]).where(Mydata.Year=='2017')
result = conn.execute(select_data_2017)
# Creating list of dictionaries where year = 2017
resultset = []
for row in result:
    resultset.append(dict(row))
# Removing null values     
newset = []
for res in resultset:
    r = {k: v for k, v in res.items() if v != '..'}
    newset.append(r)
# Creating list of dictionaries with destination, origin countries, ..
data_2017 = []
for res in resultset:
    select_data_2017 = {}
    select_data_2017['destination'] = res.pop('Destination',None)
    print(select_data_2017['destination'])
#     if select_data_2017['destination']  == None:
# #         print("Dest")
#         continue
    select_data_2017['year'] = res.pop('Year',None)
    select_data_2017['code'] = res.pop('Code',None)
    select_data_2017['index'] = res.pop('index',None)
    select_data_2017['origin'] = {k: v for k, v in res.items() if v != '..'}
#     if select_data_2017['origin']  == None:
# #         print("Origin")
#         continue
    data_2017.append(select_data_2017)    

Burundi
Comoros
Djibouti
Eritrea
Ethiopia
Kenya
Madagascar
Malawi
Mauritius
Mayotte
Mozambique
Réunion
Rwanda
Seychelles
Somalia
South Sudan
Uganda
United Republic of Tanzania
Zambia
Zimbabwe
Angola
Cameroon
Central African Republic
Chad
Congo
Democratic Republic of the Congo
Equatorial Guinea
Gabon
Sao Tome and Principe
Algeria
Egypt
Libya
Morocco
Sudan
Tunisia
Western Sahara
Botswana
Lesotho
Namibia
South Africa
Swaziland
Benin
Burkina Faso
Cabo Verde
Côte d'Ivoire
Gambia
Ghana
Guinea
Guinea-Bissau
Liberia
Mali
Mauritania
Niger
Nigeria
Saint Helena
Senegal
Sierra Leone
Togo
Kazakhstan
Kyrgyzstan
Tajikistan
Turkmenistan
Uzbekistan
China
China, Hong Kong SAR
China, Macao SAR
Dem. People's Republic of Korea
Japan
Mongolia
Republic of Korea
Afghanistan
Bangladesh
Bhutan
India
Iran (Islamic Republic of)
Maldives
Nepal
Pakistan
Sri Lanka
Brunei Darussalam
Cambodia
Indonesia
Lao People's Democratic Republic
Malaysia
Myanmar
Philippines
Singapore
Thailand
Timor-Leste
Viet Nam
Armenia
Azerbai

In [8]:
pprint(data_2017)

[{'code': 108,
  'destination': 'Burundi',
  'index': 1392,
  'origin': {'Belgium': '625',
             'Democratic Republic of the Congo': '173,417',
             'France': '312',
             'Kenya': '1,066',
             'Rwanda': '66,530',
             'Uganda': '921',
             'United Republic of Tanzania': '28,951'},
  'year': 2017},
 {'code': 174,
  'destination': 'Comoros',
  'index': 1393,
  'origin': {'France': '482',
             'Kenya': '76',
             'Madagascar': '9,651',
             'R\xe9union': '850',
             'United Republic of Tanzania': '145'},
  'year': 2017},
 {'code': 262,
  'destination': 'Djibouti',
  'index': 1394,
  'origin': {'Ethiopia': '12,732', 'Somalia': '96,137', 'Yemen': '273'},
  'year': 2017},
 {'code': 232,
  'destination': 'Eritrea',
  'index': 1395,
  'origin': {'Angola': '348',
             'Burundi': '1,052',
             'China': '135',
             'Comoros': '193',
             'Democratic Republic of the Congo': '1,698',
    

             'Zambia': '30,662'},
  'year': 2017},
 {'code': 24,
  'destination': 'Angola',
  'index': 1412,
  'origin': {'Cabo Verde': '62,498',
             'Chad': '216',
             'Congo': '7,189',
             'C\xf4te d'Ivoire': '274',
             'Democratic Republic of the Congo': '258,105',
             'Guinea': '2,284',
             'Mozambique': '1,692',
             'Namibia': '6,046',
             'Portugal': '92,793',
             'Rwanda': '7,264',
             'Sao Tome and Principe': '54,516',
             'South Africa': '42,688',
             'Zambia': '2,092'},
  'year': 2017},
 {'code': 120,
  'destination': 'Cameroon',
  'index': 1413,
  'origin': {'Angola': '2,777',
             'Benin': '2,608',
             'Canada': '193',
             'Central African Republic': '285,641',
             'Chad': '76,601',
             'Congo': '3,209',
             'Democratic Republic of the Congo': '4,431',
             'Equatorial Guinea': '3,648',
             'France'

             'Egypt': '1,159',
             'France': '8,784',
             'Germany': '1,477',
             'Iraq': '648',
             'Italy': '2,246',
             'Libya': '9,302',
             'Mali': '1,015',
             'Mauritania': '538',
             'Morocco': '5,901',
             'Nigeria': '553',
             'Senegal': '417',
             'State of Palestine': '562',
             'Syrian Arab Republic': '1,252',
             'United States of America': '619'},
  'year': 2017},
 {'code': 732,
  'destination': 'Western Sahara',
  'index': 1427,
  'origin': {'Algeria': '81',
             'France': '278',
             'Guinea': '991',
             'Guinea-Bissau': '1,046',
             'Mali': '387',
             'Mauritania': '563',
             'Senegal': '1,814'},
  'year': 2017},
 {'code': 72,
  'destination': 'Botswana',
  'index': 1428,
  'origin': {'Angola': '3,677',
             'Australia': '464',
             'Canada': '432',
             'China': '4,382',
      

  'origin': {'Algeria': '537',
             'Benin': '20,924',
             'Burkina Faso': '22,577',
             'Cameroon': '487',
             'Chad': '883',
             'C\xf4te d'Ivoire': '1,657',
             'Ghana': '1,962',
             'Libya': '183',
             'Mali': '90,580',
             'Nigeria': '98,849',
             'Senegal': '1,343',
             'Sudan': '618',
             'Togo': '11,336'},
  'year': 2017},
 {'code': 566,
  'destination': 'Nigeria',
  'index': 1445,
  'origin': {'Benin': '362,544',
             'Cameroon': '27,699',
             'Chad': '30,050',
             'Ghana': '229,048',
             'Liberia': '21,157',
             'Mali': '165,795',
             'Niger': '116,114',
             'Sierra Leone': '4,195',
             'Togo': '152,128'},
  'year': 2017},
 {'code': 654,
  'destination': 'Saint Helena',
  'index': 1446,
  'origin': {'South Africa': '107', 'United Kingdom': '398'},
  'year': 2017},
 {'code': 686,
  'destination': 'Sene

             'Russian Federation': '30',
             'Singapore': '126',
             'Sri Lanka': '48',
             'Thailand': '31,791',
             'United Kingdom': '94',
             'United States of America': '201',
             'Viet Nam': '37,601'},
  'year': 2017},
 {'code': 360,
  'destination': 'Indonesia',
  'index': 1473,
  'origin': {'Australia': '11,094',
             'Canada': '2,193',
             'China': '73,971',
             'India': '12,252',
             'Japan': '19,345',
             'Jordan': '12,252',
             'Libya': '2,315',
             'Malaysia': '2,315',
             'Netherlands': '7,110',
             'Pakistan': '8,412',
             'Philippines': '4,117',
             'Republic of Korea': '32,677',
             'Saudi Arabia': '2,315',
             'Singapore': '23,045',
             'Syrian Arab Republic': '2,315',
             'Thailand': '23,045',
             'Timor-Leste': '23,045',
             'United Kingdom': '32,026',
           

...

             'El Salvador': '1,130',
             'Equatorial Guinea': '395',
             'Eritrea': '646',
             'Estonia': '922',
             'Ethiopia': '8,806',
             'Faeroe Islands': '5',
             'Fiji': '158',
             'Finland': '3,886',
             'Gabon': '20,080',
             'Gambia': '1,935',
             'Georgia': '7,698',
             'Germany': '237,178',
             'Ghana': '6,797',
             'Gibraltar': '70',
             'Greece': '13,085',
             'Greenland': '12',
             'Guatemala': '3,039',
             'Guinea': '30,667',
             'Guinea-Bissau': '3,111',
             'Guyana': '4,792',
             'Haiti': '75,467',
             'Honduras': '594',
             'Hungary': '10,712',
             'Iceland': '389',
             'India': '48,791',
             'Indonesia': '5,021',
             'Iran (Islamic Republic of)': '23,134',
             'Iraq': '6,212',
             'Ireland': '9,977',
             'Isle

  'year': 2017},
 {'code': 92,
  'destination': 'British Virgin Islands',
  'index': 1553,
  'origin': {'Antigua and Barbuda': '789',
             'Australia': '23',
             'Bahamas': '26',
             'Barbados': '190',
             'Canada': '245',
             'Dominica': '1,283',
             'Dominican Republic': '1,782',
             'France': '23',
             'Germany': '60',
             'Guyana': '2,363',
             'India': '40',
             'Jamaica': '1,983',
             'Lebanon': '23',
             'Montserrat': '219',
             'Puerto Rico': '547',
             'Saint Kitts and Nevis': '1,418',
             'Saint Lucia': '538',
             'Saint Vincent and the Grenadines': '2,300',
             'Trinidad and Tobago': '420',
             'United Kingdom': '834',
             'United States of America': '1,796'},
  'year': 2017},
 {'code': 535,
  'destination': 'Caribbean Netherlands',
  'index': 1554,
  'origin': {'Anguilla': '29',
             'Antig

             'Germany': '665',
             'Greenland': '414',
             'Haiti': '14',
             'Honduras': '8,726',
             'Indonesia': '41',
             'Iran (Islamic Republic of)': '18',
             'Israel': '136',
             'Italy': '382',
             'Japan': '152',
             'Lebanon': '26',
             'Mexico': '18,250',
             'Netherlands': '145',
             'Nicaragua': '8,908',
             'Pakistan': '27',
             'Panama': '312',
             'Paraguay': '61',
             'Peru': '475',
             'Philippines': '69',
             'Portugal': '30',
             'Puerto Rico': '105',
             'Republic of Korea': '1,858',
             'Saudi Arabia': '33',
             'Spain': '1,373',
             'State of Palestine': '47',
             'Sweden': '48',
             'Switzerland': '160',
             'Syrian Arab Republic': '81',
             'Turkey': '26',
             'United Kingdom': '232',
             'United States 

 {'code': 170,
  'destination': 'Colombia',
  'index': 1586,
  'origin': {'Afghanistan': '122',
             'Albania': '52',
             'Algeria': '26',
             'Andorra': '49',
             'Angola': '56',
             'Anguilla': '43',
             'Antigua and Barbuda': '41',
             'Argentina': '3,419',
             'Aruba': '328',
             'Australia': '234',
             'Austria': '222',
             'Belgium': '464',
             'Bolivia (Plurinational State of)': '874',
             'Brazil': '2,496',
             'Bulgaria': '90',
             'Canada': '1,051',
             'Chile': '2,162',
             'China': '2,176',
             'China, Hong Kong SAR': '36',
             'Costa Rica': '1,128',
             'Croatia': '60',
             'Cuba': '1,945',
             'Cura\xe7ao': '97',
             'Czechia': '41',
             'Dem. People's Republic of Korea': '213',
             'Denmark': '97',
             'Dominica': '52',
             'Dominica

             'Gibraltar': '552',
             'Greece': '132,680',
             'Grenada': '133',
             'Guadeloupe': '33',
             'Guam': '110',
             'Guatemala': '520',
             'Guinea': '884',
             'Guyana': '697',
             'Haiti': '99',
             'Honduras': '287',
             'Hungary': '24,255',
             'Iceland': '807',
             'India': '408,880',
             'Indonesia': '88,095',
             'Iran (Islamic Republic of)': '51,054',
             'Iraq': '65,831',
             'Ireland': '105,925',
             'Isle of Man': '364',
             'Israel': '12,763',
             'Italy': '220,235',
             'Jamaica': '1,349',
             'Japan': '55,733',
             'Jordan': '6,591',
             'Kazakhstan': '1,780',
             'Kenya': '18,714',
             'Kiribati': '685',
             'Kuwait': '6,403',
             'Kyrgyzstan': '464',
             'Lao People's Democratic Republic': '12,697',
            

In [9]:
# Finding all country codes
country_code = []
for value in session.query(Mydata.Code).distinct():
     for index, row in df.iterrows():
        if value[0] == row['Code']:
            p = {}
            p['code'] = row['Code']
            p['country'] = row['Destination']
            country_code.append(p)

In [10]:
# Finding unique country codes
unique_country_codes = []

for c in country_code:
    if c not in unique_country_codes:
        if {k: v for k, v in c.items() if v is not None}:
            unique_country_codes.append(c)

In [11]:
# pprint(unique_country_codes)

In [27]:
# Find country code by name
def getCountryCode(country):
    for c in country_code:
        for k,v in c.items():
            if v == country:
#                 print(country)
#                 print(c['code'])
                return c['code']

In [46]:
# Get latitude from country code
def getLatLng(country):
    print(country)
    code = int(getCountryCode(country))
#     print(code)
    for l in latlng:
        for k, v in l.items():
            if(k == 'code'):
                if v == code:
#                     print(v)
#                     print(code)
#                     print(l)
#                     print([l['longitude'], l['latitude']])
                    return [l['longitude'], l['latitude']]


In [14]:
# Create JSON File which countains country code, name , latitude and longitude
df_lat_long = pd.read_csv('Country_Codes_Latitude_Longitude.csv')
latlng = []
for value in session.query(Mydata.Code).distinct():
     for index, row in df_lat_long.iterrows():
        if value[0] == row['Numeric code']:
            p = {}
            p['code'] = row['Numeric code']
            p['country'] = row['Country']
            p['latitude'] = row['Latitude (average)']
            p['longitude'] = row['Longitude (average)']
            latlng.append(p)
with open("latlng.json","w") as f:
    json.dump(latlng,f)
# pprint(latlng)

[{'code': 108, 'country': 'Burundi', 'latitude': -3.5, 'longitude': 30.0},
 {'code': 174, 'country': 'Comoros', 'latitude': -12.1667, 'longitude': 44.25},
 {'code': 262, 'country': 'Djibouti', 'latitude': 11.5, 'longitude': 43.0},
 {'code': 232, 'country': 'Eritrea', 'latitude': 15.0, 'longitude': 39.0},
 {'code': 231, 'country': 'Ethiopia', 'latitude': 8.0, 'longitude': 38.0},
 {'code': 404, 'country': 'Kenya', 'latitude': 1.0, 'longitude': 38.0},
 {'code': 450, 'country': 'Madagascar', 'latitude': -20.0, 'longitude': 47.0},
 {'code': 454, 'country': 'Malawi', 'latitude': -13.5, 'longitude': 34.0},
 {'code': 480,
  'country': 'Mauritius',
  'latitude': -20.2833,
  'longitude': 57.55},
 {'code': 175,
  'country': 'Mayotte',
  'latitude': -12.8333,
  'longitude': 45.1667},
 {'code': 508, 'country': 'Mozambique', 'latitude': -18.25, 'longitude': 35.0},
 {'code': 638, 'country': 'Réunion', 'latitude': -21.1, 'longitude': 55.6},
 {'code': 646, 'country': 'Rwanda', 'latitude': -2.0, 'longit

In [15]:
# Color code according to number of migrants
def getcolor(migrants):
#     migrants = int(migrants.replace(',', ''))
    if migrants >= 600000:
        return "#d7191c"
    elif migrants < 500000 and migrants >= 60000:
        return "#fdae61"
    elif migrants < 25000 and migrants >= 500000:
        return "#ffffbf"
    elif migrants < 10000 and migrants >= 25000:
        return "#abdda4"
    else:
        return "#2b83ba"
    
    

In [44]:
# Create dictionary for using in the plugin
data_for_plugin_2017 = []
for d in data_2017:
    data_dict = {}
    for k, v in d['origin'].items():
        data_dict['to'] = getLatLng(d['destination']) 
        if data_dict['to'] is None:
            data_dict = {}
            continue
#         print(k)
        data_dict['from'] = getLatLng(k)
        data_dict['labels'] = [d['destination'], k]
        v = int(v.replace(',', ''))
        data_dict['color'] = getcolor(v) 
        data_dict['migrants'] = v
        data_dict['arcWidth'] = 0.1
        data_dict['pulseBorderWidth'] = 0.15
        data_dict['year'] = d['year']
#         print(data_dict['from'])
        for k1, v1 in data_dict.items():
            if data_dict['to'] is not None:              
                data_for_plugin_2017.append(data_dict)
#             else:
#                 print(data_dict)

# pprint(data_for_plugin_2017)

Burundi
108
108
{'code': 108, 'country': 'Burundi', 'latitude': -3.5, 'longitude': 30.0}
[30.0, -3.5]
Belgium
56
56
{'code': 56, 'country': 'Belgium', 'latitude': 50.8333, 'longitude': 4.0}
[4.0, 50.8333]
Burundi
108
108
{'code': 108, 'country': 'Burundi', 'latitude': -3.5, 'longitude': 30.0}
[30.0, -3.5]
Democratic Republic of the Congo
180
180
{'code': 180, 'country': 'Congo, the Democratic Republic of the', 'latitude': 0.0, 'longitude': 25.0}
[25.0, 0.0]
Burundi
108
108
{'code': 108, 'country': 'Burundi', 'latitude': -3.5, 'longitude': 30.0}
[30.0, -3.5]
France
250
250
{'code': 250, 'country': 'France', 'latitude': 46.0, 'longitude': 2.0}
[2.0, 46.0]
Burundi
108
108
{'code': 108, 'country': 'Burundi', 'latitude': -3.5, 'longitude': 30.0}
[30.0, -3.5]
Kenya
404
404
{'code': 404, 'country': 'Kenya', 'latitude': 1.0, 'longitude': 38.0}
[38.0, 1.0]
Burundi
108
108
{'code': 108, 'country': 'Burundi', 'latitude': -3.5, 'longitude': 30.0}
[30.0, -3.5]
Rwanda
646
646
{'code': 646, 'country'

Kenya
404
404
{'code': 404, 'country': 'Kenya', 'latitude': 1.0, 'longitude': 38.0}
[38.0, 1.0]
Uganda
800
800
{'code': 800, 'country': 'Uganda', 'latitude': 1.0, 'longitude': 32.0}
[32.0, 1.0]
Mozambique
508
508
{'code': 508, 'country': 'Mozambique', 'latitude': -18.25, 'longitude': 35.0}
[35.0, -18.25]
Uganda
800
800
{'code': 800, 'country': 'Uganda', 'latitude': 1.0, 'longitude': 32.0}
[32.0, 1.0]
Netherlands
528
528
{'code': 528, 'country': 'Netherlands', 'latitude': 52.5, 'longitude': 5.75}
[5.75, 52.5]
Uganda
800
800
{'code': 800, 'country': 'Uganda', 'latitude': 1.0, 'longitude': 32.0}
[32.0, 1.0]
Pakistan
586
586
{'code': 586, 'country': 'Pakistan', 'latitude': 30.0, 'longitude': 70.0}
[70.0, 30.0]
Uganda
800
800
{'code': 800, 'country': 'Uganda', 'latitude': 1.0, 'longitude': 32.0}
[32.0, 1.0]
Republic of Korea
410
410
{'code': 410, 'country': 'Korea, Republic of', 'latitude': 37.0, 'longitude': 127.5}
[127.5, 37.0]
Uganda
800
800
{'code': 800, 'country': 'Uganda', 'latitude':

140
{'code': 140, 'country': 'Central African Republic', 'latitude': 7.0, 'longitude': 21.0}
[21.0, 7.0]
Cyprus
196
196
{'code': 196, 'country': 'Cyprus', 'latitude': 35.0, 'longitude': 33.0}
[33.0, 35.0]
Central African Republic
140
140
{'code': 140, 'country': 'Central African Republic', 'latitude': 7.0, 'longitude': 21.0}
[21.0, 7.0]
Democratic Republic of the Congo
180
180
{'code': 180, 'country': 'Congo, the Democratic Republic of the', 'latitude': 0.0, 'longitude': 25.0}
[25.0, 0.0]
Central African Republic
140
140
{'code': 140, 'country': 'Central African Republic', 'latitude': 7.0, 'longitude': 21.0}
[21.0, 7.0]
Denmark
208
208
{'code': 208, 'country': 'Denmark', 'latitude': 56.0, 'longitude': 10.0}
[10.0, 56.0]
Central African Republic
140
140
{'code': 140, 'country': 'Central African Republic', 'latitude': 7.0, 'longitude': 21.0}
[21.0, 7.0]
Egypt
818
818
{'code': 818, 'country': 'Egypt', 'latitude': 27.0, 'longitude': 30.0}
[30.0, 27.0]
Central African Republic
140
140
{'cod

818
{'code': 818, 'country': 'Egypt', 'latitude': 27.0, 'longitude': 30.0}
[30.0, 27.0]
Belgium
56
56
{'code': 56, 'country': 'Belgium', 'latitude': 50.8333, 'longitude': 4.0}
[4.0, 50.8333]
Egypt
818
818
{'code': 818, 'country': 'Egypt', 'latitude': 27.0, 'longitude': 30.0}
[30.0, 27.0]
Benin
204
204
{'code': 204, 'country': 'Benin', 'latitude': 9.5, 'longitude': 2.25}
[2.25, 9.5]
Egypt
818
818
{'code': 818, 'country': 'Egypt', 'latitude': 27.0, 'longitude': 30.0}
[30.0, 27.0]
Bosnia and Herzegovina
70
70
{'code': 70, 'country': 'Bosnia and Herzegovina', 'latitude': 44.0, 'longitude': 18.0}
[18.0, 44.0]
Egypt
818
818
{'code': 818, 'country': 'Egypt', 'latitude': 27.0, 'longitude': 30.0}
[30.0, 27.0]
Brazil
76
76
{'code': 76, 'country': 'Brazil', 'latitude': -10.0, 'longitude': -55.0}
[-55.0, -10.0]
Egypt
818
818
{'code': 818, 'country': 'Egypt', 'latitude': 27.0, 'longitude': 30.0}
[30.0, 27.0]
Brunei Darussalam
96
96
{'code': 96, 'country': 'Brunei Darussalam', 'latitude': 4.5, 'long

Syrian Arab Republic
760
760
{'code': 760, 'country': 'Syrian Arab Republic', 'latitude': 35.0, 'longitude': 38.0}
[38.0, 35.0]
Egypt
818
818
{'code': 818, 'country': 'Egypt', 'latitude': 27.0, 'longitude': 30.0}
[30.0, 27.0]
Tajikistan
762
762
{'code': 762, 'country': 'Tajikistan', 'latitude': 39.0, 'longitude': 71.0}
[71.0, 39.0]
Egypt
818
818
{'code': 818, 'country': 'Egypt', 'latitude': 27.0, 'longitude': 30.0}
[30.0, 27.0]
TFYR Macedonia
807
807
{'code': 807, 'country': 'Macedonia, the former Yugoslav Republic of', 'latitude': 41.8333, 'longitude': 22.0}
[22.0, 41.8333]
Egypt
818
818
{'code': 818, 'country': 'Egypt', 'latitude': 27.0, 'longitude': 30.0}
[30.0, 27.0]
Thailand
764
764
{'code': 764, 'country': 'Thailand', 'latitude': 15.0, 'longitude': 100.0}
[100.0, 15.0]
Egypt
818
818
{'code': 818, 'country': 'Egypt', 'latitude': 27.0, 'longitude': 30.0}
[30.0, 27.0]
Tunisia
788
788
{'code': 788, 'country': 'Tunisia', 'latitude': 34.0, 'longitude': 9.0}
[9.0, 34.0]
Egypt
818
818
{'

...

36
36
{'code': 36, 'country': 'Australia', 'latitude': -27.0, 'longitude': 133.0}
[133.0, -27.0]
Jamaica
388
388
{'code': 388, 'country': 'Jamaica', 'latitude': 18.25, 'longitude': -77.5}
[-77.5, 18.25]
Australia
36
36
{'code': 36, 'country': 'Australia', 'latitude': -27.0, 'longitude': 133.0}
[133.0, -27.0]
Japan
392
392
{'code': 392, 'country': 'Japan', 'latitude': 36.0, 'longitude': 138.0}
[138.0, 36.0]
Australia
36
36
{'code': 36, 'country': 'Australia', 'latitude': -27.0, 'longitude': 133.0}
[133.0, -27.0]
Jordan
400
400
{'code': 400, 'country': 'Jordan', 'latitude': 31.0, 'longitude': 36.0}
[36.0, 31.0]
Australia
36
36
{'code': 36, 'country': 'Australia', 'latitude': -27.0, 'longitude': 133.0}
[133.0, -27.0]
Kazakhstan
398
398
{'code': 398, 'country': 'Kazakhstan', 'latitude': 48.0, 'longitude': 68.0}
[68.0, 48.0]
Australia
36
36
{'code': 36, 'country': 'Australia', 'latitude': -27.0, 'longitude': 133.0}
[133.0, -27.0]
Kenya
404
404
{'code': 404, 'country': 'Kenya', 'latitude': 1

[32.0, 1.0]
Australia
36
36
{'code': 36, 'country': 'Australia', 'latitude': -27.0, 'longitude': 133.0}
[133.0, -27.0]
Ukraine
804
804
{'code': 804, 'country': 'Ukraine', 'latitude': 49.0, 'longitude': 32.0}
[32.0, 49.0]
Australia
36
36
{'code': 36, 'country': 'Australia', 'latitude': -27.0, 'longitude': 133.0}
[133.0, -27.0]
United Arab Emirates
784
784
{'code': 784, 'country': 'United Arab Emirates', 'latitude': 24.0, 'longitude': 54.0}
[54.0, 24.0]
Australia
36
36
{'code': 36, 'country': 'Australia', 'latitude': -27.0, 'longitude': 133.0}
[133.0, -27.0]
United Kingdom
826
826
{'code': 826, 'country': 'United Kingdom', 'latitude': 54.0, 'longitude': -2.0}
[-2.0, 54.0]
Australia
36
36
{'code': 36, 'country': 'Australia', 'latitude': -27.0, 'longitude': 133.0}
[133.0, -27.0]
United Republic of Tanzania
834
834
{'code': 834, 'country': 'Tanzania, United Republic of', 'latitude': -6.0, 'longitude': 35.0}
[35.0, -6.0]
Australia
36
36
{'code': 36, 'country': 'Australia', 'latitude': -27.0,

{'code': 586, 'country': 'Pakistan', 'latitude': 30.0, 'longitude': 70.0}
[70.0, 30.0]
New Zealand
554
554
{'code': 554, 'country': 'New Zealand', 'latitude': -41.0, 'longitude': 174.0}
[174.0, -41.0]
Papua New Guinea
598
598
{'code': 598, 'country': 'Papua New Guinea', 'latitude': -6.0, 'longitude': 147.0}
[147.0, -6.0]
New Zealand
554
554
{'code': 554, 'country': 'New Zealand', 'latitude': -41.0, 'longitude': 174.0}
[174.0, -41.0]
Philippines
608
608
{'code': 608, 'country': 'Philippines', 'latitude': 13.0, 'longitude': 122.0}
[122.0, 13.0]
New Zealand
554
554
{'code': 554, 'country': 'New Zealand', 'latitude': -41.0, 'longitude': 174.0}
[174.0, -41.0]
Poland
616
616
{'code': 616, 'country': 'Poland', 'latitude': 52.0, 'longitude': 20.0}
[20.0, 52.0]
New Zealand
554
554
{'code': 554, 'country': 'New Zealand', 'latitude': -41.0, 'longitude': 174.0}
[174.0, -41.0]
Republic of Korea
410
410
{'code': 410, 'country': 'Korea, Republic of', 'latitude': 37.0, 'longitude': 127.5}
[127.5, 37.0

{'code': 392, 'country': 'Japan', 'latitude': 36.0, 'longitude': 138.0}
[138.0, 36.0]
Northern Mariana Islands
580
580
{'code': 580, 'country': 'Northern Mariana Islands', 'latitude': 15.2, 'longitude': 145.75}
[145.75, 15.2]
Marshall Islands
584
584
{'code': 584, 'country': 'Marshall Islands', 'latitude': 9.0, 'longitude': 168.0}
[168.0, 9.0]
Northern Mariana Islands
580
580
{'code': 580, 'country': 'Northern Mariana Islands', 'latitude': 15.2, 'longitude': 145.75}
[145.75, 15.2]
Micronesia (Fed. States of)
583
583
{'code': 583, 'country': 'Micronesia, Federated States of', 'latitude': 6.9167, 'longitude': 158.25}
[158.25, 6.9167]
Northern Mariana Islands
580
580
{'code': 580, 'country': 'Northern Mariana Islands', 'latitude': 15.2, 'longitude': 145.75}
[145.75, 15.2]
Nepal
524
524
{'code': 524, 'country': 'Nepal', 'latitude': 28.0, 'longitude': 84.0}
[84.0, 28.0]
Northern Mariana Islands
580
580
{'code': 580, 'country': 'Northern Mariana Islands', 'latitude': 15.2, 'longitude': 145.7

540
{'code': 540, 'country': 'New Caledonia', 'latitude': -21.5, 'longitude': 165.5}
[165.5, -21.5]
Wallis and Futuna Islands
876
876
{'code': 876, 'country': 'Wallis and Futuna', 'latitude': -13.3, 'longitude': -176.2}
[-176.2, -13.3]
Vanuatu
548
548
{'code': 548, 'country': 'Vanuatu', 'latitude': -16.0, 'longitude': 167.0}
[167.0, -16.0]


In [47]:
with open("data2017.json","w") as f:
    json.dump(data_for_plugin_2017,f)

In [45]:

list_2 = []

for d in data_for_plugin_2017:
    for k1, v1 in d.items():
            if d['from'] is not None: 
                if d not in list_2:            
                    list_2.append(d)
pprint(list_2)

[{'arcWidth': 0.1,
  'color': '#2b83ba',
  'from': [35.0, -6.0],
  'labels': ['Burundi', 'United Republic of Tanzania'],
  'migrants': 28951,
  'pulseBorderWidth': 0.15,
  'to': [30.0, -3.5],
  'year': 2017},
 {'arcWidth': 0.1,
  'color': '#2b83ba',
  'from': [35.0, -6.0],
  'labels': ['Comoros', 'United Republic of Tanzania'],
  'migrants': 145,
  'pulseBorderWidth': 0.15,
  'to': [44.25, -12.1667],
  'year': 2017},
 {'arcWidth': 0.1,
  'color': '#2b83ba',
  'from': [48.0, 15.0],
  'labels': ['Djibouti', 'Yemen'],
  'migrants': 273,
  'pulseBorderWidth': 0.15,
  'to': [43.0, 11.5],
  'year': 2017},
 {'arcWidth': 0.1,
  'color': '#2b83ba',
  'from': [30.0, -20.0],
  'labels': ['Eritrea', 'Zimbabwe'],
  'migrants': 326,
  'pulseBorderWidth': 0.15,
  'to': [39.0, 15.0],
  'year': 2017},
 {'arcWidth': 0.1,
  'color': '#2b83ba',
  'from': [48.0, 15.0],
  'labels': ['Ethiopia', 'Yemen'],
  'migrants': 153,
  'pulseBorderWidth': 0.15,
  'to': [38.0, 8.0],
  'year': 2017},
 {'arcWidth': 0.1,


  'labels': ['Faeroe Islands', 'United States of America'],
  'migrants': 42,
  'pulseBorderWidth': 0.15,
  'to': [-7.0, 62.0],
  'year': 2017},
 {'arcWidth': 0.1,
  'color': '#2b83ba',
  'from': [30.0, -20.0],
  'labels': ['Finland', 'Zimbabwe'],
  'migrants': 111,
  'pulseBorderWidth': 0.15,
  'to': [26.0, 64.0],
  'year': 2017},
 {'arcWidth': 0.1,
  'color': '#2b83ba',
  'from': [30.0, -20.0],
  'labels': ['Iceland', 'Zimbabwe'],
  'migrants': 12,
  'pulseBorderWidth': 0.15,
  'to': [-18.0, 65.0],
  'year': 2017},
 {'arcWidth': 0.1,
  'color': '#2b83ba',
  'from': [30.0, -20.0],
  'labels': ['Ireland', 'Zimbabwe'],
  'migrants': 3331,
  'pulseBorderWidth': 0.15,
  'to': [-8.0, 53.0],
  'year': 2017},
 {'arcWidth': 0.1,
  'color': '#2b83ba',
  'from': [-97.0, 38.0],
  'labels': ['Isle of Man', 'United States of America'],
  'migrants': 279,
  'pulseBorderWidth': 0.15,
  'to': [-4.55, 54.23],
  'year': 2017},
 {'arcWidth': 0.1,
  'color': '#2b83ba',
  'from': [30.0, -20.0],
  'labels'

  'pulseBorderWidth': 0.15,
  'to': [147.0, -6.0],
  'year': 2017},
 {'arcWidth': 0.1,
  'color': '#2b83ba',
  'from': [167.0, -16.0],
  'labels': ['Solomon Islands', 'Vanuatu'],
  'migrants': 64,
  'pulseBorderWidth': 0.15,
  'to': [159.0, -8.0],
  'year': 2017},
 {'arcWidth': 0.1,
  'color': '#2b83ba',
  'from': [-2.0, 54.0],
  'labels': ['Vanuatu', 'United Kingdom'],
  'migrants': 109,
  'pulseBorderWidth': 0.15,
  'to': [167.0, -16.0],
  'year': 2017},
 {'arcWidth': 0.1,
  'color': '#2b83ba',
  'from': [106.0, 16.0],
  'labels': ['Guam', 'Viet Nam'],
  'migrants': 363,
  'pulseBorderWidth': 0.15,
  'to': [144.7833, 13.4667],
  'year': 2017},
 {'arcWidth': 0.1,
  'color': '#2b83ba',
  'from': [-97.0, 38.0],
  'labels': ['Kiribati', 'United States of America'],
  'migrants': 41,
  'pulseBorderWidth': 0.15,
  'to': [173.0, 1.4167],
  'year': 2017},
 {'arcWidth': 0.1,
  'color': '#2b83ba',
  'from': [-97.0, 38.0],
  'labels': ['Marshall Islands', 'United States of America'],
  'migrant

In [40]:
# list_2
# Sorted list
sorted_list = sorted(list_2, key=itemgetter('migrants'), reverse=True) 

# pprint(sorted_list)

In [41]:
with open("data_for_plugin_2017.json","w") as f:
    json.dump(list_2,f)

In [42]:
# Get the name of all columns into a list
origin_country_list = Mydata.__table__.columns.keys()

with open('countries.txt', 'w') as f:
    for item in origin_country_list:
        print(item)
#         f.write("%s\n" % item)

index
Year
Destination
Code
Afghanistan
Albania
Algeria
American Samoa
Andorra
Angola
Anguilla
Antigua and Barbuda
Argentina
Armenia
Aruba
Australia
Austria
Azerbaijan
Bahamas
Bahrain
Bangladesh
Barbados
Belarus
Belgium
Belize
Benin
Bermuda
Bhutan
Bolivia (Plurinational State of)
Bosnia and Herzegovina
Botswana
Brazil
British Virgin Islands
Brunei Darussalam
Bulgaria
Burkina Faso
Burundi
Cabo Verde
Cambodia
Cameroon
Canada
Caribbean Netherlands
Cayman Islands
Central African Republic
Chad
Channel Islands
Chile
China
China, Hong Kong SAR
China, Macao SAR
Colombia
Comoros
Congo
Cook Islands
Costa Rica
Côte d'Ivoire
Croatia
Cuba
Curaçao
Cyprus
Czechia
Dem. People's Republic of Korea
Democratic Republic of the Congo
Denmark
Djibouti
Dominica
Dominican Republic
Ecuador
Egypt
El Salvador
Equatorial Guinea
Eritrea
Estonia
Ethiopia
Faeroe Islands
Falkland Islands (Malvinas)
Fiji
Finland
France
French Guiana
French Polynesia
Gabon
Gambia
Georgia
Germany
Ghana
Gibraltar
Greece
Greenland
Grenada
